In [1]:
from datasets import list_datasets

/home/codete/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
datasets_list = list_datasets()

/tmp/ipykernel_13795/3387996211.py:1: FutureWarning: list_datasets is deprecated and will be removed in the next major version of datasets. Use 'huggingface_hub.list_datasets' instead.
  datasets_list = list_datasets()


In [3]:
from datasets import load_dataset
dataset = load_dataset('wikipedia', "20220301.simple", cache_dir="./datasets")

In [4]:
train_set = dataset['train']

In [5]:
import random

terms = random.choices(list(train_set['title']),k=1000)

In [ ]:
terms

In [7]:
import spacy

nlp = spacy.load("en_core_web_sm")

In [8]:
def sent_pos(pos_list, sentence):
    doc = nlp(sentence)
    for token in doc:
        pos_list.append(token.pos_)
    return pos_list

In [10]:
pos_ids = {
    "": 0,
    "ADJ": 1,
    "ADP": 2,
    "ADV": 3,
    "AUX": 4,
    "CONJ": 5,
    "CCONJ": 6,
    "DET": 7,
    "INTJ": 8,
    "NOUN": 9,
    "NUM": 10,
    "PART": 11,
    "PRON": 12,
    "PROPN": 13,
    "PUNCT": 14,
    "SCONJ": 15,
    "SYM": 16,
    "VERB": 17,
    "X": 18,
    "EOL": 19,
    "SPACE": 20
}

In [11]:
def pos_to_ts(pos_list):
    pos_list = sent_pos([],pos_list)
    txt_ts = []
    for pos in pos_list:
        txt_ts.append(pos_ids[pos])
    return txt_ts

#pos_to_ts(pos_list)

In [16]:
import pandas as pd

dict = {'term': terms}

df = pd.DataFrame(dict)

df.to_csv('terms.csv')

In [38]:
response_gpt3.choices[0].message.content

"Schiller Park, Illinois, is a village located in Cook County, just northwest of the city of Chicago. It has a population of approximately 11,000 residents. The village is named after the German poet Friedrich Schiller and was initially settled by German immigrants in the late 19th century.\n\nSchiller Park is conveniently situated near major transportation routes, including O'Hare International Airport and several interstate highways. This makes the village a strategic location for businesses and travelers. The airport also impacts the local economy, as many residents work in the aviation and hospitality industries.\n\nThe village offers a mix of residential, commercial, and industrial areas. Residents have access to various amenities, including parks, schools, and community centers. The Schiller Woods forest preserve, located adjacent to the village, provides opportunities for outdoor recreation such as hiking, biking, and picnicking.\n\nSchiller Park also hosts several annual events

In [40]:
from openai._client import OpenAI

client = OpenAI(
        api_key="",
)

sentences = 10

watermarking_data = pd.DataFrame()

for term in terms:        
    q = "Please explain in "+str(sentences)+" sentences as a plain text the term: " + term + ". Please do not use bullet points"
    response_gpt3 = client.chat.completions.create(model="gpt-3.5-turbo", messages=[{"role": "system", "content": q},{"role": "user", "content": q}])            
    response_gpt4 = client.chat.completions.create(model="gpt-4", messages=[{"role": "system", "content": q}, {"role": "user", "content": q}])                        
    print("Model gpt3: " + str(term) + " : " + str(response_gpt3.choices[0].message.content))
    print("Model gpt4: " + str(term) + " : " + str(response_gpt4.choices[0].message.content))
    
    personas_row4 = {'model': 'gpt4', 'prompt': prompt, 'term': term, 'response': response_gpt4.choices[0].message.content, 'pos': pos_to_ts(response_gpt4.choices[0].message.content)}
    personas_row3 = {'model': 'gpt3', 'prompt': prompt, 'term': term, 'response': response_gpt3.choices[0].message.content, 'pos': pos_to_ts(response_gpt3.choices[0].message.content)}

    watermarking_data = pd.concat([watermarking_data, pd.DataFrame([personas_row4])], ignore_index=True)
    watermarking_data = pd.concat([watermarking_data, pd.DataFrame([personas_row3])], ignore_index=True)
watermarking_data.to_csv('dane_gpt.csv')

Model gpt3: Schiller Park, Illinois : Schiller Park, Illinois is a village located in Cook County, a suburban county in the northeastern part of the state. It is situated approximately 15 miles northwest of downtown Chicago. The village covers an area of about 2.8 square miles.

Schiller Park has a population of around 11,000 people, according to the most recent census data. The village is primarily residential, with a mix of single-family homes, townhouses, and apartment buildings. There are also some commercial areas and industrial parks within the village.

One of the notable features of Schiller Park is its proximity to O'Hare International Airport, one of the busiest airports in the world. This has both positive and negative impacts on the village. On one hand, it provides convenient access to air travel, but on the other hand, it can also bring noise and congestion.

The village is served by several schools, including Schiller Park School District 81, which operates an elementary

In [23]:
from gpt4all import GPT4All
import pandas as pd

# 
models = ['llama-2-7b-chat.ggmlv3.q4_0.bin']

sentences = 10

watermarking_data = pd.DataFrame()


for model_name in models:    
    for term in terms:  
        model = GPT4All(model_name)
        with model.chat_session():        
            prompt = "Please explain in "+str(sentences)+" sentences as a plain text the term: " + term + ". Please do not use bullet points"
            print(prompt)
            response = model.generate(prompt = prompt)
            print(response)
            watermarking_row = {'model': model_name, 'prompt': prompt, 'term': term, 'response': response, 'pos': pos_to_ts(response)}
           # watermarking_data = watermarking_data.append(watermarking_row, ignore_index = True)
            watermarking_data = pd.concat([watermarking_data, pd.DataFrame([watermarking_row])], ignore_index=True)
#            watermarking_data['prompt']
    watermarking_data.to_csv("dane"+model_name+".csv")

Found model file at  /home/codete/.cache/gpt4all/llama-2-7b-chat.ggmlv3.q4_0.bin


llama.cpp: loading model from /home/codete/.cache/gpt4all/llama-2-7b-chat.ggmlv3.q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 32000
llama_model_load_internal: n_ctx      = 2048
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 256
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size = 3615.73 MB
llama_model_load_internal: mem required  = 4013.73 MB (+ 1024.00 MB per state)
llama_new_context_with_model: kv self size

Please explain in 10 sentences as a plain text the term: Schiller Park, Illinois. Please do not use bullet points
 Sure! Here is an explanation of Schiller Park, Illinois in 10 sentences:

Schiller Park is a village located in Cook County, Illinois, United States. It has a population of around 17,000 people and covers an area of approximately 2 square miles. The village was incorporated in 1924 and named after the nearby Schiller Lake. Schiller Park is known for its historic homes and buildings, including the Schiller House Museum, which dates back to the early 19th century. The village has a diverse economy with a mix of small businesses, restaurants, and light industry. Schiller Park is located approximately 20 miles northwest of Chicago and is accessible via major highways such as Interstate 90 and Illinois Route 83. The village has its own school district and offers various recreational programs for residents of all ages. Schiller Park is a family-friendly community with a strong
F

llama.cpp: loading model from /home/codete/.cache/gpt4all/llama-2-7b-chat.ggmlv3.q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 32000
llama_model_load_internal: n_ctx      = 2048
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 256
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size = 3615.73 MB
llama_model_load_internal: mem required  = 4013.73 MB (+ 1024.00 MB per state)
llama_new_context_with_model: kv self size

Please explain in 10 sentences as a plain text the term: Alf Ramsey. Please do not use bullet points
 Sure! Here is an explanation of the term "Alf Ramsey" in 10 sentences:

Alf Ramsey was a British football player and manager who was born on Christmas Day in 1920. He played as a centre-half for several clubs, including Manchester United and Leicester City, before retiring in 1964. As a manager, he led Ipswich Town to the Football League title in 1978 and won the European Cup Winners' Cup with the club in 1971. Ramsey was known for his disciplinarian style of management and his ability to get the best out of his players. He was also known for his distinctive moustache, which became a trademark feature during his playing and managerial career. Despite his successes on the pitch, Ramsey faced criticism for his strict tactics and his perceived lack of empathy towards his players. Nevertheless,
Found model file at  /home/codete/.cache/gpt4all/llama-2-7b-chat.ggmlv3.q4_0.bin


...

Please explain in 10 sentences as a plain text the term: École nationale des chartes. Please do not use bullet points
 Sure! Here is an explanation of the term "École nationale des chartes" in 10 sentences:

The École nationale des chartes (ENC) is a French graduate school specializing in the study and preservation of historical documents, manuscripts, and archives. Founded in 1930, it is one of the leading institutions for the training of professional conservators and curators in France. The ENC offers a two-year master's program that covers topics such as book conservation, paper conservation, photograph conservation, and digital preservation. Students at the ENC have access to state-of-the-art facilities and equipment, including laboratories for bookbinding, paper repair, and photographic processing. The school also maintains partnerships with numerous cultural institutions in France and abroad, providing students with opportunities for internships and professional development. Grad

llama.cpp: loading model from /home/codete/.cache/gpt4all/llama-2-7b-chat.ggmlv3.q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 32000
llama_model_load_internal: n_ctx      = 2048
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 256
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size = 3615.73 MB
llama_model_load_internal: mem required  = 4013.73 MB (+ 1024.00 MB per state)
llama_new_context_with_model: kv self size

Please explain in 10 sentences as a plain text the term: Bass-baritone. Please do not use bullet points
 Certainly! Here is an explanation of the term "bass-baritone" in 10 sentences:

A bass-baritone is a type of singing voice that falls between the bass and baritone voices. It is characterized by its deep, rich tone and its ability to produce both powerful low notes and smooth high notes with ease. Bass-baritones are often sought after in classical music, particularly in operas and choral works, as they can provide a strong foundation for the lower parts of a vocal ensemble while also adding depth and warmth to the upper ranges. The range of a bass-baritone typically spans from around C3 to A2, with some singers able to reach as low as B2 or as high as E3. Bass-baritones are known for their versatility and can excel in a variety of musical styles, including classical, jazz, and pop. They often have a wide vocal
Found model file at  /home/codete/.cache/gpt4all/llama-2-7b-chat.ggmlv3.q

llama.cpp: loading model from /home/codete/.cache/gpt4all/llama-2-7b-chat.ggmlv3.q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 32000
llama_model_load_internal: n_ctx      = 2048
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 256
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size = 3615.73 MB
llama_model_load_internal: mem required  = 4013.73 MB (+ 1024.00 MB per state)
llama_new_context_with_model: kv self size

Please explain in 10 sentences as a plain text the term: The Art of Worldly Wisdom: A Pocket Oracle. Please do not use bullet points
 Certainly! Here is an explanation of "The Art of Worldly Wisdom: A Pocket Oracle" in 10 sentences:

"The Art of Worldly Wisdom: A Pocket Oracle" is a book that serves as a guide to living a wise and fulfilling life. It offers practical advice on how to navigate the challenges of everyday life with grace, humor, and insight. The book is divided into short, bite-sized chapters, each of which covers a different aspect of worldly wisdom, such as dealing with change, finding inner peace, and building meaningful relationships.

The author, Ben Franklin, was a true Renaissance man - a statesman, inventor, writer, and philosopher who lived in the 18th century. He drew upon his vast knowledge and experience to create this book, which has stood the test of time as a timeless classic on wisdom and living well.

Fran


In [24]:
from gpt4all import GPT4All
import pandas as pd

# 
models = ['ggml-model-gpt4all-falcon-q4_0.bin']

sentences = 10

watermarking_data = pd.DataFrame()


for model_name in models:    
    for term in terms:  
        model = GPT4All(model_name)
        with model.chat_session():        
            prompt = "Please explain in "+str(sentences)+" sentences as a plain text the term: " + term + ". Please do not use bullet points"
            print(prompt)
            response = model.generate(prompt = prompt)
            print(response)
            watermarking_row = {'model': model_name, 'prompt': prompt, 'term': term, 'response': response, 'pos': pos_to_ts(response)}
           # watermarking_data = watermarking_data.append(watermarking_row, ignore_index = True)
            watermarking_data = pd.concat([watermarking_data, pd.DataFrame([watermarking_row])], ignore_index=True)
#            watermarking_data['prompt']
    watermarking_data.to_csv("dane"+model_name+".csv")

Found model file at  /home/codete/.cache/gpt4all/ggml-model-gpt4all-falcon-q4_0.bin
falcon_model_load: loading model from '/home/codete/.cache/gpt4all/ggml-model-gpt4all-falcon-q4_0.bin' - please wait ...
falcon_model_load: n_vocab   = 65024
falcon_model_load: n_embd    = 4544
falcon_model_load: n_head    = 71
falcon_model_load: n_head_kv = 1
falcon_model_load: n_layer   = 32
falcon_model_load: ftype     = 2
falcon_model_load: qntvr     = 0
falcon_model_load: ggml ctx size = 3872.64 MB
falcon_model_load: memory_size =    32.00 MB, n_mem = 65536
falcon_model_load: ........................ done
falcon_model_load: model size =  3872.59 MB / num tensors = 196
Please explain in 10 sentences as a plain text the term: Schiller Park, Illinois. Please do not use bullet points
Schiiller Park is located in the state of Illinois in the United States. It is a residential community with homes and apartments for rent or sale. The park itself offers amenities such as playgrounds, tennis courts, basket

In [25]:
from gpt4all import GPT4All
import pandas as pd

# 
models = ['orca-mini-13b.ggmlv3.q4_0.bin']

sentences = 10

watermarking_data = pd.DataFrame()


for model_name in models:    
    for term in terms:  
        model = GPT4All(model_name)
        with model.chat_session():        
            prompt = "Please explain in "+str(sentences)+" sentences as a plain text the term: " + term + ". Please do not use bullet points"
            print(prompt)
            response = model.generate(prompt = prompt)
            print(response)
            watermarking_row = {'model': model_name, 'prompt': prompt, 'term': term, 'response': response, 'pos': pos_to_ts(response)}
           # watermarking_data = watermarking_data.append(watermarking_row, ignore_index = True)
            watermarking_data = pd.concat([watermarking_data, pd.DataFrame([watermarking_row])], ignore_index=True)
#            watermarking_data['prompt']
    watermarking_data.to_csv("dane"+model_name+".csv")

Found model file at  /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin


llama.cpp: loading model from /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 32000
llama_model_load_internal: n_ctx      = 2048
llama_model_load_internal: n_embd     = 5120
llama_model_load_internal: n_mult     = 256
llama_model_load_internal: n_head     = 40
llama_model_load_internal: n_head_kv  = 40
llama_model_load_internal: n_layer    = 40
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 13824
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 13B
llama_model_load_internal: ggml ctx size = 6983.72 MB
llama_model_load_internal: mem required  = 7477.72 MB (+ 1600.00 MB per state)
llama_new_context_with_model: kv self size 

Please explain in 10 sentences as a plain text the term: Schiller Park, Illinois. Please do not use bullet points
 Schiller Park is a park located in the city of Chicago, Illinois, USA. It is named after German poet and writer William Shakespeare and is known for its beautiful scenery and outdoor recreational activities such as picnicking, fishing, and hiking. The park also features several cultural events throughout the year, including live music performances, theater plays, and art displays.
Found model file at  /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin


llama.cpp: loading model from /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 32000
llama_model_load_internal: n_ctx      = 2048
llama_model_load_internal: n_embd     = 5120
llama_model_load_internal: n_mult     = 256
llama_model_load_internal: n_head     = 40
llama_model_load_internal: n_head_kv  = 40
llama_model_load_internal: n_layer    = 40
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 13824
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 13B
llama_model_load_internal: ggml ctx size = 6983.72 MB
llama_model_load_internal: mem required  = 7477.72 MB (+ 1600.00 MB per state)
llama_new_context_with_model: kv self size 

Please explain in 10 sentences as a plain text the term: Alf Ramsey. Please do not use bullet points
 Alf Ramsey is a football manager who was born on January 1, 1964, in Blackpool, England. He began his career as a player and later became a coach, working with several clubs including Manchester United, Chelsea, and the England national team. Ramsey is known for his attacking style of play and his ability to develop young talent. He has won numerous awards throughout his career, including the Premier League Manager of the Month award in 2019.
Found model file at  /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin


...

Please explain in 10 sentences as a plain text the term: École nationale des chartes. Please do not use bullet points
 The Ecole nationale des chartes is a French higher education institution that specializes in training professionals in the field of charting and mapping. It offers courses and programs for students who want to pursue careers in fields such as urban planning, environmental management, and transportation. The Ecole nationale des chartes has a rich history and reputation in France and around the world.
Found model file at  /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin


llama.cpp: loading model from /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 32000
llama_model_load_internal: n_ctx      = 2048
llama_model_load_internal: n_embd     = 5120
llama_model_load_internal: n_mult     = 256
llama_model_load_internal: n_head     = 40
llama_model_load_internal: n_head_kv  = 40
llama_model_load_internal: n_layer    = 40
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 13824
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 13B
llama_model_load_internal: ggml ctx size = 6983.72 MB
llama_model_load_internal: mem required  = 7477.72 MB (+ 1600.00 MB per state)
llama_new_context_with_model: kv self size 

Please explain in 10 sentences as a plain text the term: Bass-baritone. Please do not use bullet points
 The term "Bass-baritone" refers to a male voice that is deep and rich, with a lower range than a tenor but higher than a bass. It falls in between the voices of tenor and bass, and is often used for male characters in musical theater or for singing in choral groups. The term was first popularized by the American baritone Marian Anderson, who was known for her powerful and resonant voice.
Found model file at  /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin


llama.cpp: loading model from /home/codete/.cache/gpt4all/orca-mini-13b.ggmlv3.q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 32000
llama_model_load_internal: n_ctx      = 2048
llama_model_load_internal: n_embd     = 5120
llama_model_load_internal: n_mult     = 256
llama_model_load_internal: n_head     = 40
llama_model_load_internal: n_head_kv  = 40
llama_model_load_internal: n_layer    = 40
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 13824
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 13B
llama_model_load_internal: ggml ctx size = 6983.72 MB
llama_model_load_internal: mem required  = 7477.72 MB (+ 1600.00 MB per state)
llama_new_context_with_model: kv self size 

Please explain in 10 sentences as a plain text the term: The Art of Worldly Wisdom: A Pocket Oracle. Please do not use bullet points
 The Art of Worldly Wisdom: A Pocket Oracle is a book that teaches readers how to navigate the challenges and obstacles of life with ease. It provides practical advice on topics such as relationships, career, finance, and personal growth. The author, who was once a successful businessman, shares his own experiences and insights gained from years of success and failure. The book emphasizes the importance of taking action, being adaptable, and seeking guidance when faced with difficult situations. It also encourages readers to stay positive and focused on their goals, even in the face of adversity. Overall, The Art of Worldly Wisdom: A Pocket Oracle is a valuable resource for anyone looking to improve their lives and achieve success in all areas.


# Preprocessing



In [61]:
import pandas as pd

gpt = pd.read_csv('done-dane_gpt.csv')
llama = pd.read_csv('done-danellama-2-7b-chat.ggmlv3.q4_0.bin.csv')
orca = pd.read_csv('done-daneorca-mini-13b.ggmlv3.q4_0.bin.csv')
falcon = pd.read_csv('done-daneggml-model-gpt4all-falcon-q4_0.bin.csv')

In [62]:
gpt4 = gpt[gpt['model']=='gpt4']
gpt3 = gpt[gpt['model']=='gpt3']

In [63]:
gpt4 = gpt4[['prompt','term','response','pos']]
gpt3 = gpt[['prompt','term','response','pos']]
llama = llama[['prompt','term','response','pos']]
falcon = falcon[['prompt','term','response','pos']]
orca = orca[['prompt','term','response','pos']]

In [64]:
llama

prompt  \
0    Please explain in 10 sentences as a plain text...   
1    Please explain in 10 sentences as a plain text...   
2    Please explain in 10 sentences as a plain text...   
3    Please explain in 10 sentences as a plain text...   
4    Please explain in 10 sentences as a plain text...   
..                                                 ...   
995  Please explain in 10 sentences as a plain text...   
996  Please explain in 10 sentences as a plain text...   
997  Please explain in 10 sentences as a plain text...   
998  Please explain in 10 sentences as a plain text...   
999  Please explain in 10 sentences as a plain text...   

                                           term  \
0                       Schiller Park, Illinois   
1                                    Alf Ramsey   
2                                 Jimmy Gardner   
3                                        Fréjus   
4                   2006 Jama Masjid explosions   
..                                          ...   
995                                Dom DiMaggio   
996                                Tando Qaiser   
997                 École nationale des chartes   
998                               Bass-baritone   
999  The Art of Worldly Wisdom: A Pocket Oracle   

                                              response  \
0     Sure! Here is an explanation of Schiller Park...   
1     Sure! Here is an explanation of the term "Alf...   
2     I apologize, but I cannot provide information...   
3     Sure! Here is an explanation of the term "Fré...   
4     I apologize, but I cannot provide information...   
..                                                 ...   
995   Certainly! Here is an explanation of the term...   
996   I apologize, but I cannot provide information...   
997   Sure! Here is an explanation of the term "Éco...   
998   Certainly! Here is an explanation of the term...   
999   Certainly! Here is an explanation of "The Art...   

                                                   pos  
0    [20, 13, 14, 3, 4, 7, 9, 2, 13, 13, 14, 13, 2,...  
1    [20, 13, 14, 3, 4, 7, 9, 2, 7, 9, 14, 13, 13, ...  
2    [20, 12, 17, 14, 6, 12, 4, 11, 17, 9, 2, 7, 9,...  
3    [20, 13, 14, 3, 4, 7, 9, 2, 7, 9, 14, 13, 14, ...  
4    [20, 12, 17, 14, 6, 12, 4, 11, 17, 9, 6, 9, 12...  
..                                                 ...  
995  [20, 3, 14, 3, 4, 7, 9, 2, 7, 9, 14, 13, 13, 1...  
996  [20, 12, 17, 14, 6, 12, 4, 11, 17, 9, 2, 7, 9,...  
997  [20, 13, 14, 3, 4, 7, 9, 2, 7, 9, 14, 13, 9, 1...  
998  [20, 3, 14, 3, 4, 7, 9, 2, 7, 9, 14, 9, 14, 9,...  
999  [20, 3, 14, 3, 4, 7, 9, 2, 14, 7, 9, 2, 13, 13...  

[1000 rows x 4 columns]

In [29]:
llama.loc[[1]]['response'][1]

' Sure! Here is an explanation of the term "Alf Ramsey" in 10 sentences:\n\nAlf Ramsey was a British football player and manager who was born on Christmas Day in 1920. He played as a centre-half for several clubs, including Manchester United and Leicester City, before retiring in 1964. As a manager, he led Ipswich Town to the Football League title in 1978 and won the European Cup Winners\' Cup with the club in 1971. Ramsey was known for his disciplinarian style of management and his ability to get the best out of his players. He was also known for his distinctive moustache, which became a trademark feature during his playing and managerial career. Despite his successes on the pitch, Ramsey faced criticism for his strict tactics and his perceived lack of empathy towards his players. Nevertheless,'

In [65]:
llama['response'].replace('.*\n\n', '', regex=True, inplace = True)

In [36]:
llama.loc[2]['response']

' I apologize, but I cannot provide information on a person named "Jimmy Gardner" as there is no such individual with that name known to me or any reliable sources. It\'s possible that you may be referring to a private individual who wishes to remain anonymous, or the name could be misspelled or used in a fictional context. If you have any more information or clarification regarding Jimmy Gardner, please feel free to provide it and I will do my best to assist you.'

In [66]:
llama = llama[~llama['response'].str.contains("I apologize, but I cannot provide information", case=False)]

In [67]:
llama

prompt  \
0    Please explain in 10 sentences as a plain text...   
1    Please explain in 10 sentences as a plain text...   
3    Please explain in 10 sentences as a plain text...   
5    Please explain in 10 sentences as a plain text...   
6    Please explain in 10 sentences as a plain text...   
..                                                 ...   
994  Please explain in 10 sentences as a plain text...   
995  Please explain in 10 sentences as a plain text...   
997  Please explain in 10 sentences as a plain text...   
998  Please explain in 10 sentences as a plain text...   
999  Please explain in 10 sentences as a plain text...   

                                                  term  \
0                              Schiller Park, Illinois   
1                                           Alf Ramsey   
3                                               Fréjus   
5                                          Otsego Hall   
6    Second Amendment to the United States Constitu...   
..                                                 ...   
994        Oliver Optic's Magazine: Our Boys and Girls   
995                                       Dom DiMaggio   
997                        École nationale des chartes   
998                                      Bass-baritone   
999         The Art of Worldly Wisdom: A Pocket Oracle   

                                              response  \
0    Schiller Park is a village located in Cook Cou...   
1    Alf Ramsey was a British football player and m...   
3    Fréjus is a city located on the French Riviera...   
5    Otsego Hall is a historic building located in ...   
6     The Second Amendment to the United States Con...   
..                                                 ...   
994  Oliver Optic was a pen name used by American a...   
995  Dom DiMaggio was an American professional base...   
997  The École nationale des chartes (ENC) is a Fre...   
998  A bass-baritone is a type of singing voice tha...   
999                                               Fran   

                                                   pos  
0    [20, 13, 14, 3, 4, 7, 9, 2, 13, 13, 14, 13, 2,...  
1    [20, 13, 14, 3, 4, 7, 9, 2, 7, 9, 14, 13, 13, ...  
3    [20, 13, 14, 3, 4, 7, 9, 2, 7, 9, 14, 13, 14, ...  
5    [20, 13, 14, 3, 4, 7, 9, 2, 13, 13, 2, 10, 9, ...  
6    [20, 7, 13, 13, 2, 7, 13, 13, 13, 4, 7, 1, 9, ...  
..                                                 ...  
994  [20, 3, 14, 3, 4, 7, 9, 2, 14, 13, 13, 11, 9, ...  
995  [20, 3, 14, 3, 4, 7, 9, 2, 7, 9, 14, 13, 13, 1...  
997  [20, 13, 14, 3, 4, 7, 9, 2, 7, 9, 14, 13, 9, 1...  
998  [20, 3, 14, 3, 4, 7, 9, 2, 7, 9, 14, 9, 14, 9,...  
999  [20, 3, 14, 3, 4, 7, 9, 2, 14, 7, 9, 2, 13, 13...  

[798 rows x 4 columns]

'Schiller Park is a village located in Cook County, Illinois, United States. It has a population of around 17,000 people and covers an area of approximately 2 square miles. The village was incorporated in 1924 and named after the nearby Schiller Lake. Schiller Park is known for its historic homes and buildings, including the Schiller House Museum, which dates back to the early 19th century. The village has a diverse economy with a mix of small businesses, restaurants, and light industry. Schiller Park is located approximately 20 miles northwest of Chicago and is accessible via major highways such as Interstate 90 and Illinois Route 83. The village has its own school district and offers various recreational programs for residents of all ages. Schiller Park is a family-friendly community with a strong'

# Fractal analysis

tbd

In [75]:
!pip3 install neurokit2

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 1.9 MB/s eta 0:00:0000:0100:010m

[notice] A new release of pip is available: 23.3.1 -> 23.3.2
[notice] To update, run: pip install --upgrade pip


In [124]:
import neurokit2 as nk

a = [eval(i) for i in llama.loc[1]['pos'].split(',')]
b = [eval(i) for i in llama.loc[22]['pos'].split(',')]
c = [eval(i) for i in llama.loc[20]['pos'].split(',')]

df1, info1 = nk.complexity(a)
df2, info2 = nk.complexity(b)
df3, info3 = nk.complexity(c)

TypeError: bad operand type for unary -: 'list'

In [123]:
info1

{'Method': 'afnn',
 'Values': array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
        18, 19, 20]),
 'E1': array([       nan, 0.74828149, 0.8043003 , 0.68791874, 0.90938219,
        0.84744698, 0.84078943, 1.0137107 , 0.94886825, 0.91029526,
        0.98255064, 0.9613106 , 0.98470536, 0.99448126, 0.9748196 ,
        1.00471248, 0.99675453, 0.98168736, 0.99973882, 0.98445082]),
 'E2': array([       nan, 0.99931282, 1.02461743, 0.91657895, 1.08855691,
        1.05116687, 0.90419732, 1.12602858, 1.02629662, 0.90335196,
        0.99310345, 0.98024516, 0.99262605, 0.99644181, 1.00173533,
        1.01926089, 0.98723663, 1.03982577, 0.98099903, 1.0370604 ])}

In [113]:
llama['pos'].replace('\]', '', regex=True, inplace=True)
a = [eval(i) for i in llama.loc[1]['pos'].split(',')]

/var/folders/p4/6h9d2vxd05j4lwqtfwfw5c2h0000gn/T/ipykernel_49849/3005884342.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  llama['pos'].replace('\]', '', regex=True, inplace=True)


In [114]:
a

[20,
 13,
 14,
 3,
 4,
 7,
 9,
 2,
 7,
 9,
 14,
 13,
 13,
 14,
 2,
 10,
 9,
 14,
 20,
 13,
 13,
 4,
 7,
 1,
 9,
 9,
 6,
 9,
 12,
 4,
 17,
 2,
 13,
 13,
 2,
 10,
 14,
 12,
 17,
 2,
 7,
 9,
 14,
 9,
 2,
 1,
 9,
 14,
 17,
 13,
 13,
 6,
 13,
 13,
 14,
 2,
 17,
 2,
 10,
 14,
 2,
 7,
 9,
 14,
 12,
 17,
 13,
 13,
 2,
 7,
 13,
 13,
 9,
 2,
 10,
 6,
 17,
 7,
 13,
 13,
 13,
 11,
 13,
 2,
 7,
 9,
 2,
 10,
 14,
 13,
 4,
 17,
 2,
 12,
 1,
 9,
 2,
 9,
 6,
 12,
 9,
 11,
 17,
 7,
 1,
 2,
 2,
 12,
 9,
 14,
 12,
 4,
 3,
 17,
 2,
 12,
 1,
 9,
 14,
 12,
 17,
 7,
 9,
 9,
 2,
 12,
 9,
 6,
 1,
 9,
 14,
 15,
 12,
 9,
 2,
 7,
 9,
 14,
 13,
 17,
 9,
 2,
 12,
 1,
 9,
 6,
 12,
 17,
 9,
 2,
 9,
 2,
 12,
 9,
 14,
 3,
 14]

In [112]:
llama.loc[1]['pos'].split(',')

['20',
 '13',
 '14',
 '3',
 '4',
 '7',
 '9',
 '2',
 '7',
 '9',
 '14',
 '13',
 '13',
 '14',
 '2',
 '10',
 '9',
 '14',
 '20',
 '13',
 '13',
 '4',
 '7',
 '1',
 '9',
 '9',
 '6',
 '9',
 '12',
 '4',
 '17',
 '2',
 '13',
 '13',
 '2',
 '10',
 '14',
 '12',
 '17',
 '2',
 '7',
 '9',
 '14',
 '9',
 '2',
 '1',
 '9',
 '14',
 '17',
 '13',
 '13',
 '6',
 '13',
 '13',
 '14',
 '2',
 '17',
 '2',
 '10',
 '14',
 '2',
 '7',
 '9',
 '14',
 '12',
 '17',
 '13',
 '13',
 '2',
 '7',
 '13',
 '13',
 '9',
 '2',
 '10',
 '6',
 '17',
 '7',
 '13',
 '13',
 '13',
 '11',
 '13',
 '2',
 '7',
 '9',
 '2',
 '10',
 '14',
 '13',
 '4',
 '17',
 '2',
 '12',
 '1',
 '9',
 '2',
 '9',
 '6',
 '12',
 '9',
 '11',
 '17',
 '7',
 '1',
 '2',
 '2',
 '12',
 '9',
 '14',
 '12',
 '4',
 '3',
 '17',
 '2',
 '12',
 '1',
 '9',
 '14',
 '12',
 '17',
 '7',
 '9',
 '9',
 '2',
 '12',
 '9',
 '6',
 '1',
 '9',
 '14',
 '15',
 '12',
 '9',
 '2',
 '7',
 '9',
 '14',
 '13',
 '17',
 '9',
 '2',
 '12',
 '1',
 '9',
 '6',
 '12',
 '17',
 '9',
 '2',
 '9',
 '2',
 '12',
 '9',
 '14

In [70]:
import fathon

pydfa = fathon.DFA()

ModuleNotFoundError: No module named 'fathon'

# Stylometry

tbd

In [ ]:
!pip install stylo_metrix

In [106]:
from stylo_metrix.stylo_metrix import StyloMetrix

ModuleNotFoundError: No module named 'stylo_metrix.stylo_metrix'

In [82]:
import stylo_metrix as sm

In [89]:
from stylo_metrix.structures import CustomMetric, MetricsGroup
from stylo_metrix.utils import incidence, ratio

In [101]:
@CustomMetric(name="Third person singular verb incidence")
def VERBS_3S(doc):
    verbs = [token for token in doc
            if token.pos_ == "VBZ" ]
    result = ratio(len(verbs), doc._.n_tokens)
    debug = {"verbs": verb
            s, "n_tokens": doc._.n_tokens}
    return result, debug

result = VERBS_3S(nlp(response))

AttributeError: [E046] Can't retrieve unregistered extension attribute 'n_tokens'. Did you forget to call the `set_extension` method?